In [1]:
#https://pypi.org/project/finvizfinance/

from finvizfinance.news import News
from textblob import TextBlob

#if finvizfinance import news does not work directly, then run below command first
#pip install finvizfinance

import logging

import re
from textblob import TextBlob
from collections import Counter
import statistics

#get current date and time - Python datetime object
from datetime import datetime #headers

In [2]:
# Configure logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

In [3]:
def fetch_finviz_news():
    # Initialize the News object
    news = News()# news class is part of finfinzfinance

    # Retrieve news data
    news_data = news.get_news()
    #print(news_data)
    
     # Loop and Display the news items
    df_news = news_data['news']
    #print(df_news)
    
    print("Stock Sentiment Analysis Results:")
    for index,row in df_news.iterrows():
        logger.info(f"Time: {row['Date']}, Title: {row['Title']}, Link: {row['Link']}")
        
        #if "AAPL" not in row['Title']:
            #continue
    
        #Do sentimental analysis for each news
        #output = analyze_sentiment(row['Title'])
        
        result = analyze_stock_sentiment(row['Title'])
        
        print("=" * 50)
        print(f"News = {row['Title']}")
        for key, value in result.items():
            print(f"{key}: {value}")

In [4]:
def analyze_stock_sentiment(text):
    """
    Analyze sentiment of stock market-related news text.
    
    Args:
        text (str): News text to analyze
        
    Returns:
        dict: Comprehensive sentiment analysis results
    """
    if not text or not isinstance(text, str):
        return {"error": "Invalid input: Please provide a non-empty string"}
    
    # Clean and preprocess text
    cleaned_text = clean_text(text)
    
    # Basic TextBlob sentiment analysis
    blob = TextBlob(cleaned_text)
    polarity = blob.sentiment.polarity  # -1 (negative) to 1 (positive)
    subjectivity = blob.sentiment.subjectivity  # 0 (objective) to 1 (subjective)
    
    # Financial keyword analysis
    financial_sentiment = analyze_financial_keywords(cleaned_text)
    
    # Market direction indicators
    direction_signals = detect_market_direction(cleaned_text)
    
    # Risk indicators
    risk_indicators = detect_risk_signals(cleaned_text)
    
    # Confidence score based on multiple factors
    confidence = calculate_confidence_score(polarity, subjectivity, financial_sentiment, text)
    
    # Generate trading insights
    insights = generate_trading_insights(
        polarity, subjectivity, financial_sentiment, 
        direction_signals, risk_indicators, confidence
    )
    
    return {
        "sentiment_analysis": {
            "polarity": round(polarity, 3),
            "polarity_label": get_polarity_label(polarity),
            "subjectivity": round(subjectivity, 3),
            "subjectivity_label": get_subjectivity_label(subjectivity)
        },
        "financial_sentiment": {
            "score": round(financial_sentiment["score"], 3),
            "positive_signals": financial_sentiment["positive"],
            "negative_signals": financial_sentiment["negative"]
        },
        "market_indicators": {
            "direction_signals": direction_signals,
            "risk_level": risk_indicators["level"],
            "risk_keywords": risk_indicators["keywords"]
        },
        "confidence_score": round(confidence, 3),
        "trading_insights": insights,
        "recommendation": get_trading_recommendation(polarity, financial_sentiment, risk_indicators, confidence)
    }

def clean_text(text):
    """Clean and preprocess text for analysis."""
    # Convert to lowercase
    text = text.lower()
    # Remove extra whitespace
    text = re.sub(r'\s+', ' ', text).strip()
    # Remove special characters but keep important punctuation
    text = re.sub(r'[^\w\s\.\!\?\-\%\$]', ' ', text)
    return text

def analyze_financial_keywords(text):
    """Analyze financial-specific keywords and phrases."""
    positive_keywords = [
        'profit', 'growth', 'increase', 'rise', 'gain', 'surge', 'boom', 'bull',
        'outperform', 'beat estimates', 'exceed expectations', 'strong earnings',
        'revenue growth', 'expansion', 'acquisition', 'merger', 'dividend',
        'buyback', 'upgrade', 'positive outlook', 'recovery', 'rally'
    ]
    
    negative_keywords = [
        'loss', 'decline', 'fall', 'drop', 'crash', 'bear', 'recession',
        'bankruptcy', 'debt', 'deficit', 'downgrade', 'miss estimates',
        'below expectations', 'weak earnings', 'layoffs', 'restructuring',
        'investigation', 'scandal', 'lawsuit', 'volatility', 'uncertainty',
        'risk', 'concern', 'warning', 'plunge', 'tumble'
    ]
    
    positive_count = sum(text.count(word) for word in positive_keywords)
    negative_count = sum(text.count(word) for word in negative_keywords)
    
    # Calculate financial sentiment score
    total_keywords = positive_count + negative_count
    if total_keywords == 0:
        financial_score = 0
    else:
        financial_score = (positive_count - negative_count) / total_keywords
    
    return {
        "score": financial_score,
        "positive": [word for word in positive_keywords if word in text],
        "negative": [word for word in negative_keywords if word in text]
    }

def detect_market_direction(text):
    """Detect market direction indicators."""
    upward_indicators = ['up', 'rise', 'increase', 'gain', 'higher', 'climb', 'soar', 'jump']
    downward_indicators = ['down', 'fall', 'decrease', 'drop', 'lower', 'decline', 'sink', 'plummet']
    
    upward_count = sum(text.count(word) for word in upward_indicators)
    downward_count = sum(text.count(word) for word in downward_indicators)
    
    if upward_count > downward_count:
        direction = "bullish"
    elif downward_count > upward_count:
        direction = "bearish"
    else:
        direction = "neutral"
    
    return {
        "direction": direction,
        "upward_signals": upward_count,
        "downward_signals": downward_count
    }

def detect_risk_signals(text):
    """Detect risk-related keywords and assess risk level."""
    high_risk_keywords = [
        'bankruptcy', 'investigation', 'fraud', 'scandal', 'lawsuit',
        'regulation', 'volatile', 'crash', 'crisis', 'emergency'
    ]
    
    medium_risk_keywords = [
        'uncertainty', 'concern', 'warning', 'caution', 'risk',
        'challenge', 'pressure', 'weakness', 'slowdown'
    ]
    
    high_risk_count = sum(text.count(word) for word in high_risk_keywords)
    medium_risk_count = sum(text.count(word) for word in medium_risk_keywords)
    
    found_keywords = []
    found_keywords.extend([word for word in high_risk_keywords if word in text])
    found_keywords.extend([word for word in medium_risk_keywords if word in text])
    
    if high_risk_count > 0:
        risk_level = "high"
    elif medium_risk_count > 2:
        risk_level = "medium"
    elif medium_risk_count > 0:
        risk_level = "low"
    else:
        risk_level = "minimal"
    
    return {
        "level": risk_level,
        "keywords": found_keywords
    }

def calculate_confidence_score(polarity, subjectivity, financial_sentiment, text):
    """Calculate confidence score based on multiple factors."""
    # Base confidence from sentiment strength
    sentiment_strength = abs(polarity)
    
    # Objectivity bonus (lower subjectivity = higher confidence)
    objectivity_bonus = 1 - subjectivity
    
    # Financial keyword presence bonus
    financial_bonus = min(abs(financial_sentiment["score"]), 0.3)
    
    # Text length factor (longer text generally more reliable)
    length_factor = min(len(text.split()) / 100, 0.2)
    
    confidence = (sentiment_strength * 0.4 + 
                 objectivity_bonus * 0.3 + 
                 financial_bonus * 0.2 + 
                 length_factor * 0.1)
    
    return min(confidence, 1.0)

def generate_trading_insights(polarity, subjectivity, financial_sentiment, 
                            direction_signals, risk_indicators, confidence):
    """Generate actionable trading insights."""
    insights = []
    
    # Sentiment-based insights
    if polarity > 0.3 and confidence > 0.6:
        insights.append("Strong positive sentiment detected - potential buying opportunity")
    elif polarity < -0.3 and confidence > 0.6:
        insights.append("Strong negative sentiment detected - consider selling or shorting")
    elif abs(polarity) < 0.1:
        insights.append("Neutral sentiment - market may be consolidating")
    
    # Subjectivity insights
    if subjectivity < 0.3:
        insights.append("High objectivity in news suggests factual basis for sentiment")
    elif subjectivity > 0.7:
        insights.append("High subjectivity - sentiment may be opinion-based, trade with caution")
    
    # Financial sentiment insights
    if financial_sentiment["score"] > 0.5:
        insights.append("Strong financial indicators support positive outlook")
    elif financial_sentiment["score"] < -0.5:
        insights.append("Negative financial indicators suggest fundamental concerns")
    
    # Direction insights
    if direction_signals["direction"] == "bullish":
        insights.append("Market direction indicators suggest upward momentum")
    elif direction_signals["direction"] == "bearish":
        insights.append("Market direction indicators suggest downward pressure")
    
    # Risk insights
    if risk_indicators["level"] == "high":
        insights.append("HIGH RISK: Consider reducing position size or avoiding trade")
    elif risk_indicators["level"] == "medium":
        insights.append("Moderate risk detected - use appropriate risk management")
    
    # Confidence insights
    if confidence < 0.4:
        insights.append("Low confidence in analysis - wait for more information")
    elif confidence > 0.8:
        insights.append("High confidence in sentiment analysis")
    
    return insights

def get_polarity_label(polarity):
    """Convert polarity score to descriptive label."""
    if polarity > 0.5:
        return "Very Positive"
    elif polarity > 0.1:
        return "Positive"
    elif polarity > -0.1:
        return "Neutral"
    elif polarity > -0.5:
        return "Negative"
    else:
        return "Very Negative"

def get_subjectivity_label(subjectivity):
    """Convert subjectivity score to descriptive label."""
    if subjectivity < 0.3:
        return "Objective"
    elif subjectivity < 0.6:
        return "Somewhat Subjective"
    else:
        return "Highly Subjective"

def get_trading_recommendation(polarity, financial_sentiment, risk_indicators, confidence):
    """Generate overall trading recommendation."""
    if risk_indicators["level"] == "high":
        return "AVOID - High risk detected"
    
    if confidence < 0.4:
        return "WAIT - Low confidence, gather more information"
    
    combined_score = (polarity + financial_sentiment["score"]) / 2
    
    if combined_score > 0.3 and confidence > 0.6:
        return "BUY - Positive sentiment with good confidence"
    elif combined_score < -0.3 and confidence > 0.6:
        return "SELL - Negative sentiment with good confidence"
    else:
        return "HOLD - Mixed or weak signals"
    




In [ ]:
# use this main if you want to call news from FinViz 
if __name__ == "__main__":
    
    loop = 0
    r_ound = 0
    while loop == 0: #infinity condition
        dt = datetime.now()
        sec = dt.strftime("%S")
        secs_into_int = int(sec)
        
        if secs_into_int == 0 or secs_into_int == 30:
            r_ound = r_ound + 1 #just to make a note of number of counts we have triggered finviz
            print(f"Round = {r_ound}")
            fetch_finviz_news()
        
        
    

Round = 1


2025-11-11 12:24:00,421 - INFO - Time: 11:01PM, Title: Britannia Industries slumps after long-time MD Varun Berry steps down, Link: https://www.reuters.com/sustainability/boards-policy-regulation/britannia-industries-slumps-after-long-time-md-varun-berry-steps-down-2025-11-11/
2025-11-11 12:24:00,505 - INFO - Time: 11:00PM, Title: India's Bajaj Finance slips after cutting loan book growth forecast, Link: https://www.reuters.com/world/india/indias-bajaj-finance-slips-after-cutting-loan-book-growth-forecast-2025-11-11/
2025-11-11 12:24:00,508 - INFO - Time: 10:41PM, Title: Japan 30-Year Bond Sale Has Weaker Demand Than 12-Month Average, Link: https://www.bloomberg.com/news/articles/2025-11-11/japan-30-year-bond-sale-has-weaker-demand-than-12-month-average
2025-11-11 12:24:00,510 - INFO - Time: 10:14PM, Title: Asian Stocks Erase Gains as Chinese Shares Decline: Markets Wrap, Link: https://www.bloomberg.com/news/articles/2025-11-10/stock-market-today-dow-s-p-live-updates
2025-11-11 12:24:0

Stock Sentiment Analysis Results:
News = Britannia Industries slumps after long-time MD Varun Berry steps down
sentiment_analysis: {'polarity': -0.156, 'polarity_label': 'Negative', 'subjectivity': 0.289, 'subjectivity_label': 'Objective'}
financial_sentiment: {'score': 0, 'positive_signals': [], 'negative_signals': []}
market_indicators: {'direction_signals': {'direction': 'bearish', 'upward_signals': 0, 'downward_signals': 1}, 'risk_level': 'minimal', 'risk_keywords': []}
confidence_score: 0.286
trading_insights: ['High objectivity in news suggests factual basis for sentiment', 'Market direction indicators suggest downward pressure', 'Low confidence in analysis - wait for more information']
recommendation: WAIT - Low confidence, gather more information
News = India's Bajaj Finance slips after cutting loan book growth forecast
sentiment_analysis: {'polarity': -0.6, 'polarity_label': 'Very Negative', 'subjectivity': 0.9, 'subjectivity_label': 'Highly Subjective'}
financial_sentiment: {

2025-11-11 12:24:00,625 - INFO - Time: 07:23PM, Title: Wall Street’s biggest bull reveals what investors got wrong this year — and what’s ahead for stocks and crypto, Link: https://www.marketwatch.com/story/wall-streets-biggest-bull-reveals-what-investors-got-wrong-this-year-and-whats-ahead-for-stocks-and-crypto-e7fd79bc
2025-11-11 12:24:00,635 - INFO - Time: 07:23PM, Title: Wall Street's biggest bull reveals what investors got wrong this year, Link: https://www.marketwatch.com/bulletins/redirect/go?g=15309656-431f-4177-8b64-d26e3238fedf&mod=mw_rss_bulletins
2025-11-11 12:24:00,640 - INFO - Time: 07:01PM, Title: A battle over a Chinese chip maker that rocked the global car industry, Link: https://www.bbc.com/news/articles/cr43kyn9d6po?at_medium=RSS&at_campaign=rss
2025-11-11 12:24:00,645 - INFO - Time: 06:57PM, Title: Trump has made it very clear he wants to move forward, GOP senator says, Link: https://www.foxbusiness.com/video/6384923451112
2025-11-11 12:24:00,648 - INFO - Time: 06:5

News = Wall Street’s biggest bull reveals what investors got wrong this year — and what’s ahead for stocks and crypto
sentiment_analysis: {'polarity': -0.5, 'polarity_label': 'Very Negative', 'subjectivity': 0.9, 'subjectivity_label': 'Highly Subjective'}
financial_sentiment: {'score': 1.0, 'positive_signals': ['bull'], 'negative_signals': []}
market_indicators: {'direction_signals': {'direction': 'neutral', 'upward_signals': 0, 'downward_signals': 0}, 'risk_level': 'minimal', 'risk_keywords': []}
confidence_score: 0.309
trading_insights: ['High subjectivity - sentiment may be opinion-based, trade with caution', 'Strong financial indicators support positive outlook', 'Low confidence in analysis - wait for more information']
recommendation: WAIT - Low confidence, gather more information
News = Wall Street's biggest bull reveals what investors got wrong this year
sentiment_analysis: {'polarity': -0.5, 'polarity_label': 'Very Negative', 'subjectivity': 0.9, 'subjectivity_label': 'Highly S

...

2025-09-16 14:57:31,293 - INFO - Time: Sep-15, Title: Senate set to confirm Trump adviser Stephen Miran as Fed governor, Link: https://finance.yahoo.com/news/senate-set-to-confirm-trump-adviser-miran-as-fed-governor-in-time-for-crucial-rate-decision-174216093.html
2025-09-16 14:57:31,296 - INFO - Time: Sep-15, Title: Senate clears Trump pick Miran to  Fed board ahead of key interest rate vote, Link: https://www.bbc.com/news/articles/cgrq5x97qlqo?at_medium=RSS&at_campaign=rss
2025-09-16 14:57:31,299 - INFO - Time: Sep-15, Title: Senate confirms Stephen Miran to Fed board ahead of crucial rate cut meeting, Link: https://foxbusiness.com/politics/senate-confirms-stephen-miran-fed-board-ahead-crucial-rate-cut-meeting
2025-09-16 14:57:31,302 - INFO - Time: Sep-15, Title: Miran set to vote at this week’s Fed meeting. Here’s what to expect on Wednesday, Link: https://www.marketwatch.com/bulletins/redirect/go?g=578f7dd3-cce5-4340-b1ea-d57096361af8&mod=mw_rss_bulletins
2025-09-16 14:57:31,305 - 

Stock Sentiment Analysis Results:
News = China's $19 trillion stock market, once called uninvestable, lures foreigners again
sentiment_analysis: {'polarity': 0.0, 'polarity_label': 'Neutral', 'subjectivity': 0.0, 'subjectivity_label': 'Objective'}
financial_sentiment: {'score': 1.0, 'positive_signals': ['gain'], 'negative_signals': []}
market_indicators: {'direction_signals': {'direction': 'bullish', 'upward_signals': 1, 'downward_signals': 0}, 'risk_level': 'minimal', 'risk_keywords': []}
confidence_score: 0.371
trading_insights: ['Neutral sentiment - market may be consolidating', 'High objectivity in news suggests factual basis for sentiment', 'Strong financial indicators support positive outlook', 'Market direction indicators suggest upward momentum', 'Low confidence in analysis - wait for more information']
recommendation: WAIT - Low confidence, gather more information
News = Anglo and Codelco Agree to Jointly Develop Copper Mines in Chile
sentiment_analysis: {'polarity': 0.0, 'pol

2025-09-16 14:57:31,385 - INFO - Time: Sep-15, Title: Investment strategist shares 'very cool' way to get income from small-caps, Link: https://www.foxbusiness.com/video/6379522769112
2025-09-16 14:57:31,394 - INFO - Time: Sep-15, Title: Hedge Funds Notch Win at CFTC Over Yen Swap Clearinghouse, Link: https://www.bloomberg.com/news/articles/2025-09-15/hedge-funds-notch-win-at-cftc-over-yen-swap-clearinghouse
2025-09-16 14:57:31,397 - INFO - Time: Sep-15, Title: Alphabet’s stock was an AI loser. Now it’s beaten out Nvidia on the year., Link: https://www.marketwatch.com/bulletins/redirect/go?g=73c6708f-149b-4d50-96ba-168fed31c464&mod=mw_rss_bulletins
2025-09-16 14:57:31,400 - INFO - Time: Sep-15, Title: Sotheby’s Lands a Leonard Lauder Art Collection Worth More Than $400 Million, Link: https://www.nytimes.com/2025/09/15/arts/design/sothebys-leonard-lauder-collection.html
2025-09-16 14:57:31,404 - INFO - Time: Sep-15, Title: Football Is Coming to Saudi Arabia, Where Soccer Is King, Link: 

News = Investment strategist shares 'very cool' way to get income from small-caps
sentiment_analysis: {'polarity': 0.455, 'polarity_label': 'Positive', 'subjectivity': 0.845, 'subjectivity_label': 'Highly Subjective'}
financial_sentiment: {'score': 0, 'positive_signals': [], 'negative_signals': []}
market_indicators: {'direction_signals': {'direction': 'neutral', 'upward_signals': 0, 'downward_signals': 0}, 'risk_level': 'minimal', 'risk_keywords': []}
confidence_score: 0.239
trading_insights: ['High subjectivity - sentiment may be opinion-based, trade with caution', 'Low confidence in analysis - wait for more information']
recommendation: WAIT - Low confidence, gather more information
News = Hedge Funds Notch Win at CFTC Over Yen Swap Clearinghouse
sentiment_analysis: {'polarity': 0.8, 'polarity_label': 'Very Positive', 'subjectivity': 0.4, 'subjectivity_label': 'Somewhat Subjective'}
financial_sentiment: {'score': 0, 'positive_signals': [], 'negative_signals': []}
market_indicators: 

KeyboardInterrupt: 

In [ ]:
# Example usage - just to test one sample news
if __name__ == "__main__":
    
   # Test with sample news
    sample_news = "Apple Inc. reported strong quarterly earnings that beat analyst estimates, with revenue growing 15% year-over-year. The company announced a new dividend  increase and share buyback program. CEO highlighted robust iPhone sales and  expanding services revenue. However, some analysts expressed concerns about supply chain challenges in the coming quarter."
    result = analyze_stock_sentiment(sample_news)
        
    print("=" * 50)
    #print(f"News = {row['Title']}")
    for key, value in result.items():
        print(f"{key}: {value}")
        
    #fetch_finviz_news()